In [19]:
import pandas as pd
import numpy as np
from sklearn.model_selection import StratifiedKFold
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from imblearn.over_sampling import SMOTE
import tools
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder

In [2]:
#load data
df = pd.read_csv('duke_vital_model_imputed.csv')
df.head()
df["PostCond"].value_counts()

1    62257
0    21063
Name: PostCond, dtype: int64

In [3]:
subj_dict = tools.create_subj_dict(df)
subj_labels = np.array([np.array(list([key, subj_dict[key][0]["PostCond"]])) for key in subj_dict.keys()])
# subject_ids = subj_conds[:, 0]
# subject_labels = subj_conds[:, 1]
skf = StratifiedKFold(n_splits = 10, shuffle=True, random_state=42)
patient_split = skf.split(subj_labels[:, 0], subj_labels[:, 1])
train_patient_index = dict()
test_patient_index = dict()
cnt = 0
for train_i, test_i in patient_split:
    train_patient_index[cnt] = train_i
    test_patient_index[cnt] = test_i
    cnt += 1

In [20]:
categorical_transformer = Pipeline(
    [
        ('onehot', OneHotEncoder(handle_unknown = 'ignore'))
    ]
)
from sklearn.preprocessing import StandardScaler

numeric_transformer = Pipeline(
    [
        ('scaler', StandardScaler())
    ]
)

In [4]:
def filterer(pair):
    key, value = pair
    if len(value) >= 2:
        return True
    return False

In [44]:
# categorical_columns = ["RACE_G", "GENDER", "HXCOPD", "HXDIAB", "HXHTN", "HXHYL", "HXSMOKE"]

# train_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[train_patient_index[0], 0]}
# test_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[test_patient_index[0], 0]}

# train_df = tools.subj_dict_to_df(train_subj_dict)
# test_df = tools.subj_dict_to_df(test_subj_dict)

# trends = tools.return_trends(train_df, [[2], [3], [4], [5], [6], [7], [8], [9], [10], [11], [12], [13]], ["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

# train_col_names = list(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())
# test_col_names = list(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())

# imputer = IterativeImputer(random_state=42)

# X_train_for_imputed = imputer.fit_transform(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())
# X_test_for_imputed = imputer.transform(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())

# imputed_train_df = pd.DataFrame(X_train_for_imputed, columns=train_col_names)
# imputed_test_df = pd.DataFrame(X_test_for_imputed, columns=test_col_names)

# imputed_train_df["RSUBJID"] = train_df["RSUBJID"]
# imputed_train_df["PostCond"] = train_df["PostCond"]
# imputed_test_df["RSUBJID"] = test_df["RSUBJID"]
# imputed_test_df["PostCond"] = test_df["PostCond"]

# imputed_train_subj_dict = tools.create_subj_dict(imputed_train_df)
# imputed_test_subj_dict = tools.create_subj_dict(imputed_test_df)

# filtered_imputed_train_subj_dict = dict(filter(filterer, imputed_train_subj_dict.items()))
# filtered_imputed_test_subj_dict = dict(filter(filterer, imputed_test_subj_dict.items()))

# normalized_train_dict = tools.dist_from_age_mean(filtered_imputed_train_subj_dict, trends)
# normalized_test_dict = tools.dist_from_age_mean(filtered_imputed_test_subj_dict, trends)

# linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
# linearized_test_dict = tools.dict_to_linfit(normalized_test_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

# linearized_train_df = tools.lin_dict_to_df(linearized_train_dict)
# linearized_test_df = tools.lin_dict_to_df(linearized_test_dict)

# linearized_train_df[categorical_columns] = linearized_train_df[categorical_columns].astype(int)
# linearized_test_df[categorical_columns] = linearized_test_df[categorical_columns].astype(int)
# unique_vals = dict()
# for col in categorical_columns:
#     unique_vals[col] = np.unique(linearized_test_df[col])

# def filter_func(row):
#     for col in categorical_columns:
#         if row[col] not in unique_vals[col]:
#             return False
#     return True

# linearized_train_df = linearized_train_df[linearized_train_df.apply(filter_func, axis=1)]
# linearized_train_df.reset_index()

# # linearized_train_df = pd.get_dummies(linearized_train_df, columns=categorical_columns)
# # linearized_test_df = pd.get_dummies(linearized_test_df, columns=categorical_columns)

# print(linearized_train_df.shape)
# print(linearized_test_df.shape)

# print("linearized_train_df")
# for column in linearized_train_df.columns:
#     print(column)

# print("linearized_test_df")
# for column in linearized_test_df.columns:
#     print(column)

# X_feats = linearized_train_df.drop(labels=["RSUBJID", "PostCond"], axis=1)
# X_labels = linearized_train_df["PostCond"]
# cols = linearized_train_df.drop(labels=["RSUBJID"], axis=1).columns

# resampler = SMOTE()

# print(X_feats.shape)
# print(X_labels.shape)

# X_feats_resampled, X_labels_resampled = resampler.fit_resample(X_feats, X_labels)

# X_feats_resampled["PostCond"] = X_labels_resampled

# print("X_feats_resampled")
# for column in X_feats_resampled.columns:
#     print(column)

# X_feats_resampled[categorical_columns] = X_feats_resampled[categorical_columns].astype(int)

# X = pd.get_dummies(X_feats_resampled, columns=categorical_columns)
# X_test = pd.get_dummies(linearized_test_df.drop(labels=["RSUBJID"], axis=1), columns=categorical_columns)

# X_test = X_test[X.columns]

# print(X.shape)
# print(X_test.shape)

# for col in X.columns:
#     if col not in X_test.columns:
#         print("adding 0 column")
#         X_test[col] = 0

# for colX, colXtest in zip(X.columns, X_test.columns):
#     if colX != colXtest:
#         print(f'column mismatch: {colX}, {colXtest}')

# # X = pd.get_dummies(pd.DataFrame(np.concatenate([X_feats_resampled, np.array(X_labels_resampled).reshape(len(X_labels_resampled), 1)], axis=1), columns=cols), columns = categorical_columns)

# # X = pd.get_dummies(X_feats_resampled, columns = categorical_columns)

# # X_test = pd.get_dummies(linearized_test_df.drop(labels=["RSUBJID"], axis=1), columns=categorical_columns)

# # X = X_feats_resampled
# # X_test = linearized_test_df.drop(labels=["RSUBJID"], axis=1)
# print(X.columns)
# print(X.shape)
# print(X_test.columns)
# print(X_test.shape)

# # trends = tools.return_trends(df, [[2], [3], [4], [5], [6], [7], [8], [9], [10], [11], [12], [13]], ["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
# # train_col_names = list(df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())
# # imputer = IterativeImputer(random_state=42)
# # X_train_for_imputed = imputer.fit_transform(df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())
# # imputed_train_df = pd.DataFrame(X_train_for_imputed, columns=train_col_names)
# # imputed_train_df["RSUBJID"] = df["RSUBJID"]
# # imputed_train_df["PostCond"] = df["PostCond"]
# # imputed_train_subj_dict = tools.create_subj_dict(imputed_train_df)
# # filtered_imputed_train_subj_dict = dict(filter(filterer, imputed_train_subj_dict.items()))
# # normalized_train_dict = tools.dist_from_age_mean(filtered_imputed_train_subj_dict, trends)
# # linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
# # linearized_train_df = tools.lin_dict_to_df(linearized_train_dict)
# # X = linearized_train_df.drop(labels=["RSUBJID"], axis=1)



# train_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[train_patient_index[0], 0]}
# test_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[test_patient_index[0], 0]}

# train_df = tools.subj_dict_to_df(train_subj_dict)
# test_df = tools.subj_dict_to_df(test_subj_dict)

# trends = tools.return_trends(train_df, [[2], [3], [4], [5], [6], [7], [8], [9], [10], [11], [12], [13]], ["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

# train_col_names = list(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())
# test_col_names = list(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())

# imputer = IterativeImputer(random_state=42)

# X_train_for_imputed = imputer.fit_transform(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())
# X_test_for_imputed = imputer.transform(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())

# imputed_train_df = pd.DataFrame(X_train_for_imputed, columns=train_col_names)
# imputed_test_df = pd.DataFrame(X_test_for_imputed, columns=test_col_names)

# imputed_train_df["RSUBJID"] = train_df["RSUBJID"]
# imputed_train_df["PostCond"] = train_df["PostCond"]
# imputed_test_df["RSUBJID"] = test_df["RSUBJID"]
# imputed_test_df["PostCond"] = test_df["PostCond"]

# imputed_train_subj_dict = tools.create_subj_dict(imputed_train_df)
# imputed_test_subj_dict = tools.create_subj_dict(imputed_test_df)

# filtered_imputed_train_subj_dict = dict(filter(filterer, imputed_train_subj_dict.items()))
# filtered_imputed_test_subj_dict = dict(filter(filterer, imputed_test_subj_dict.items()))

# normalized_train_dict = tools.dist_from_age_mean(filtered_imputed_train_subj_dict, trends)
# normalized_test_dict = tools.dist_from_age_mean(filtered_imputed_test_subj_dict, trends)

# linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
# linearized_test_dict = tools.dict_to_linfit(normalized_test_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

# linearized_train_df = tools.lin_dict_to_df(linearized_train_dict)
# linearized_test_df = tools.lin_dict_to_df(linearized_test_dict)

# X = linearized_train_df.drop(labels=["RSUBJID"], axis=1)
# X_test = linearized_test_df.drop(labels=["RSUBJID"], axis=1)





train_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[train_patient_index[0], 0]}
test_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[test_patient_index[0], 0]}

train_df = tools.subj_dict_to_df(train_subj_dict)
test_df = tools.subj_dict_to_df(test_subj_dict)

trends = tools.return_trends(train_df, [[2], [3], [4], [5], [6], [7], [8], [9], [10], [11], [12], [13]], ["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

train_col_names = list(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())
test_col_names = list(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())

imputer = IterativeImputer(random_state=42)

X_train_for_imputed = imputer.fit_transform(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())
X_test_for_imputed = imputer.transform(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())

print(np.count_nonzero(np.isnan(X_train_for_imputed)))
print(np.count_nonzero(np.isnan(X_train_for_imputed)))

imputed_train_df = pd.DataFrame(X_train_for_imputed, columns=train_col_names)
imputed_test_df = pd.DataFrame(X_test_for_imputed, columns=test_col_names)

imputed_train_df["RSUBJID"] = train_df["RSUBJID"]
imputed_train_df["PostCond"] = train_df["PostCond"]
imputed_test_df["RSUBJID"] = test_df["RSUBJID"]
imputed_test_df["PostCond"] = test_df["PostCond"]
print(imputed_train_df.isna().any().any())
print(imputed_test_df.isna().any().any())

imputed_train_subj_dict = tools.create_subj_dict(imputed_train_df)
imputed_test_subj_dict = tools.create_subj_dict(imputed_test_df)

print(f'imputed_train_subj_dict: {tools.check_subj_dict_dim_err(imputed_train_subj_dict)}')

filtered_imputed_train_subj_dict = dict(filter(filterer, imputed_train_subj_dict.items()))
filtered_imputed_test_subj_dict = dict(filter(filterer, imputed_test_subj_dict.items()))

print(f'filtered_imputed_train_subj_dict: {tools.check_subj_dict_dim_err(filtered_imputed_train_subj_dict)}')

normalized_train_dict = tools.dist_from_age_mean(filtered_imputed_train_subj_dict, trends)
normalized_test_dict = tools.dist_from_age_mean(filtered_imputed_test_subj_dict, trends)

print(f'normalized_train_dict: {tools.check_subj_dict_dim_err(normalized_train_dict)}')
print(tools.subj_dict_nan(normalized_train_dict))

# def check_nans_row_lst(pair):
#     key, lst = pair
#     return any(list(map(lambda x: any(list(map(lambda n: np.isnan(n[1]), x.items()))), lst)))

linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
linearized_test_dict = tools.dict_to_linfit(normalized_test_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

print(tools.check_lin_dict_dim_err(linearized_train_dict))
print(tools.lin_dict_nan(linearized_train_dict))

linearized_train_df = tools.lin_dict_to_df(linearized_train_dict)
linearized_test_df = tools.lin_dict_to_df(linearized_test_dict)

print(linearized_train_df.isna().any().any())

X_train_i_df = linearized_train_df.drop(labels=["RSUBJID", "PostCond"], axis=1)
X_test_i_df = linearized_test_df.drop(labels=["RSUBJID", "PostCond"], axis=1)
y_train_i = linearized_train_df["PostCond"]
y_test_i = linearized_test_df["PostCond"]

categorical_columns = ["RACE_G", "GENDER", "HXCOPD", "HXDIAB", "HXHTN", "HXHYL", "HXSMOKE"]
numeric_columns = [col for col in X_train_i_df.columns if col not in categorical_columns]

preprocessor = ColumnTransformer(
    [
        ('categoricals', categorical_transformer, categorical_columns),
        ('numericals', numeric_transformer, numeric_columns)
    ],
    remainder = 'passthrough',
    sparse_threshold=0
)

print(X_train_i_df.isna().any().any())

X_train_i = preprocessor.fit_transform(X_train_i_df)
X_test_i = preprocessor.transform(X_test_i_df)

print(np.count_nonzero(np.isnan(X_train_i)))
print(np.count_nonzero(np.isnan(y_train_i)))



# X_train_i = X[train_i]
# X_test_i = X[test_i]
# y_train_i = y[train_i]
# y_test_i = y[test_i]

resampler = SMOTE()

print(f'train len before resample: {len(X_train_i)}')
X_train_i, y_train_i = resampler.fit_resample(X_train_i, y_train_i)
print(f'train len after resample: {len(X_train_i)}')
print(f'Num of positive train: {np.sum(y_train_i)}')
print(f'Num of negative train: {len(y_train_i) - np.sum(y_train_i)}')

X_train = X_train_i
X_test = X_test_i
y_train = y_train_i
y_test = y_test_i

0
0
False
False
imputed_train_subj_dict: False
filtered_imputed_train_subj_dict: False
normalized_train_dict: False
False


/var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/ipykernel_89406/3359774009.py:231: RankWarning: Polyfit may be poorly conditioned
  linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
/var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/ipykernel_89406/3359774009.py:231: RankWarning: Polyfit may be poorly conditioned
  linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
/var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/ipykernel_89406/3359774009.py:231: RankWarning: Polyfit may be poorly conditioned
  linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WE

False
False
False
False
0
0
train len before resample: 15312
train len after resample: 23396
Num of positive train: 11698.0
Num of negative train: 11698.0


In [9]:
print(X.shape)
# X.to_csv("train_ds_resampled2.csv")
# X_test.to_csv("test_ds_resampled2.csv")

(15312, 70)


In [47]:
from importlib import reload
import torch
import net
reload(net)
# X_train = torch.tensor(X.drop(labels=["PostCond"], axis=1).to_numpy())
# y_train = torch.tensor(X["PostCond"])
# X_test_tensor = torch.tensor(X_test.drop(labels=["PostCond"], axis=1).to_numpy())
# y_test = torch.tensor(X_test["PostCond"])

nn = net.MyANN(X_train.shape[1], 16)
net.train(torch.tensor(X_train), torch.tensor(y_train), nn, torch.tensor(X_test), torch.tensor(y_test), init_lr = 0.01)

In epoch 0, loss: 0.695, train_acc: 0.498, train_bal_acc: 0.498, train_recall: 0.995, train_precision: 0.499, val acc: 0.766, bal acc: 0.502, val recall: 0.998, val precision: 0.767
In epoch 5, loss: 0.664, train_acc: 0.648, train_bal_acc: 0.648, train_recall: 0.567, train_precision: 0.678, val acc: 0.591, bal acc: 0.626, val recall: 0.559, val precision: 0.857
In epoch 10, loss: 0.621, train_acc: 0.665, train_bal_acc: 0.665, train_recall: 0.559, train_precision: 0.709, val acc: 0.589, bal acc: 0.633, val recall: 0.550, val precision: 0.864
In epoch 15, loss: 0.597, train_acc: 0.677, train_bal_acc: 0.677, train_recall: 0.620, train_precision: 0.700, val acc: 0.625, bal acc: 0.635, val recall: 0.616, val precision: 0.853
In epoch 20, loss: 0.582, train_acc: 0.686, train_bal_acc: 0.686, train_recall: 0.649, train_precision: 0.701, val acc: 0.634, bal acc: 0.627, val recall: 0.640, val precision: 0.844
In epoch 25, loss: 0.572, train_acc: 0.693, train_bal_acc: 0.693, train_recall: 0.671, 